In [2]:
import torch
import numpy as np
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import matplotlib.pyplot as plt
import time
import sys
from scipy.sparse import linalg
from pathlib import Path
if torch.cuda.is_available():  
    device = "cuda" 
else:  
    device = "cpu" 

pi = torch.tensor(np.pi,dtype=torch.float64)
torch.set_default_tensor_type(torch.DoubleTensor)

class model(nn.Module):
    """ ReLU k shallow neural network
    Parameters: 
    input size: input dimension
    hidden_size1 : number of hidden layers 
    num_classes: output classes 
    k: degree of relu functions
    """
    def __init__(self, input_size, hidden_size1, num_classes,k = 1):
        super().__init__()
        self.fc1 = nn.Linear(input_size, hidden_size1)
        self.fc2 = nn.Linear(hidden_size1, num_classes,bias = False)
        self.k = k 
    def forward(self, x):
        u1 = self.fc2(F.relu(self.fc1(x))**self.k)
        return u1

def plot_2D(f, Nx = 400, Ny = 400): 

    x, y = np.meshgrid(np.linspace(0, 1, Nx), np.linspace(0, 1, Ny), indexing='xy')
    xy_comb = np.stack((x.flatten(),y.flatten())).T
    xy_comb = torch.tensor(xy_comb)
    z = f(xy_comb).reshape(Nx,Ny)
    z = z.detach().numpy()
    plt.figure(dpi=200)
    ax = plt.axes(projection='3d')
    ax.plot_surface(x , y , z )
    plt.show()

def plot_subdomains(my_model):
    x_coord =torch.linspace(0,1,200)
    wi = my_model.fc1.weight.data
    bi = my_model.fc1.bias.data 
    for i, bias in enumerate(bi):  
        if wi[i,1] !=0: 
            plt.plot(x_coord, - wi[i,0]/wi[i,1]*x_coord - bias/wi[i,1])
        else: 
            plt.plot(x_coord,  - bias/wi[i,0]*torch.ones(x_coord.size()))

    plt.xlim([0,1])
    plt.ylim([0,1])
    plt.legend()
    plt.show()
    return 0    

def PiecewiseGQ2D(target, Nx, order): 
    """
    Parameters
    ----------
    target : 
        Target function 
    Nx: int 
        number of intervals along the dimension. No Ny, assume Nx = Ny
    order: int 
        order of the Gauss Quadrature
    """

#     print("order: ",order )
    x, w = np.polynomial.legendre.leggauss(order)
    gauss_pts = np.array(np.meshgrid(x,x,indexing='ij')).reshape(2,-1).T
    weights =  (w*w[:,None]).ravel()

    gauss_pts =torch.tensor(gauss_pts)
    weights = torch.tensor(weights)

    h = 1/Nx # 100 intervals 
    long_weights =  torch.tile(weights,(Nx**2,1))
    long_weights = long_weights.reshape(-1,1)
    long_weights = long_weights * h**2 /4 

    integration_points = torch.tile(gauss_pts,(Nx**2,1))
    scale_factor = h/2 
    integration_points = scale_factor * integration_points

    index = np.arange(1,Nx+1)-0.5
    ordered_pairs = np.array(np.meshgrid(index,index,indexing='ij'))
    ordered_pairs = ordered_pairs.reshape(2,-1).T

    # print(ordered_pairs)
    # print()
    ordered_pairs = torch.tensor(ordered_pairs)
    # print(ordered_pairs.size())
    ordered_pairs = torch.tile(ordered_pairs, (1,order**2)) # number of GQ points
    # print(ordered_pairs)

    ordered_pairs =  ordered_pairs.reshape(-1,2)
    # print(ordered_pairs)
    translation = ordered_pairs*h 
    # print(translation)

    integration_points = integration_points + translation 
    integration_points = integration_points.to(device)
#     print(integration_points.size())
    # func_values = integrand2_torch(integration_points)
    func_values = target(integration_points) # .to(device)
#     print("func values size ",func_values.size())

    long_weights = long_weights.to(device)
    integral_value = long_weights.T@func_values # this allows multiple functions, stored in columns
    return integral_value


def PiecewiseGQ2D_weights_points(Nx, order): 
    """ A slight modification of PiecewiseGQ2D function that only needs the weights and integration points.
    Parameters
    ----------

    Nx: int 
        number of intervals along the dimension. No Ny, assume Nx = Ny
    order: int 
        order of the Gauss Quadrature

    Returns
    -------
    long_weights: torch.tensor
    integration_points: torch.tensor
    """

#     print("order: ",order )
    x, w = np.polynomial.legendre.leggauss(order)
    gauss_pts = np.array(np.meshgrid(x,x,indexing='ij')).reshape(2,-1).T
    weights =  (w*w[:,None]).ravel()

    gauss_pts =torch.tensor(gauss_pts)
    weights = torch.tensor(weights)

    h = 1/Nx # 100 intervals 
    long_weights =  torch.tile(weights,(Nx**2,1))
    long_weights = long_weights.reshape(-1,1)
    long_weights = long_weights * h**2 /4 

    integration_points = torch.tile(gauss_pts,(Nx**2,1))
    scale_factor = h/2 
    integration_points = scale_factor * integration_points

    index = np.arange(1,Nx+1)-0.5
    ordered_pairs = np.array(np.meshgrid(index,index,indexing='ij'))
    ordered_pairs = ordered_pairs.reshape(2,-1).T

    # print(ordered_pairs)
    # print()
    ordered_pairs = torch.tensor(ordered_pairs)
    # print(ordered_pairs.size())
    ordered_pairs = torch.tile(ordered_pairs, (1,order**2)) # number of GQ points
    # print(ordered_pairs)

    ordered_pairs =  ordered_pairs.reshape(-1,2)
    # print(ordered_pairs)
    translation = ordered_pairs*h 
    # print(translation)

    integration_points = integration_points + translation 
#     print(integration_points.size())
    # func_values = integrand2_torch(integration_points)
    return long_weights.to(device), integration_points.to(device)

def minimize_linear_layer_explicit_assemble(model,target,weights, integration_points,solver="direct"):
    """
    calls the following functions (dependency): 
    1. GQ_piecewise_2D
    input: the nn model containing parameter 
    1. define the loss function  
    2. take derivative to extract the linear system A
    3. call the cg solver in scipy to solve the linear system 
    output: sol. solution of Ax = b
    """
    start_time = time.time() 
    w = model.fc1.weight.data 
    b = model.fc1.bias.data 
    basis_value_col = F.relu(integration_points @ w.t()+ b)**(model.k) 
    weighted_basis_value_col = basis_value_col * weights 
    jac = weighted_basis_value_col.t() @ basis_value_col 
     
    rhs = weighted_basis_value_col.t() @ (target(integration_points)) 
    print("assembling the matrix time taken: ", time.time()-start_time) 
    start_time = time.time()    
    if solver == "cg": 
        sol, exit_code = linalg.cg(np.array(jac.detach().cpu()),np.array(rhs.detach().cpu()),tol=1e-12)
        sol = torch.tensor(sol).view(1,-1)
    elif solver == "direct": 
#         sol = np.linalg.inv( np.array(jac.detach().cpu()) )@np.array(rhs.detach().cpu())
        sol = (torch.linalg.solve( jac.detach(), rhs.detach())).view(1,-1)
    elif solver == "ls":
        sol = (torch.linalg.lstsq(jac.detach().cpu(),rhs.detach().cpu(),driver='gelsd').solution).view(1,-1)
        # sol = (torch.linalg.lstsq(jac.detach(),rhs.detach()).solution).view(1,-1) # gpu/cpu, driver = 'gels', cannot solve singular
    print("solving Ax = b time taken: ", time.time()-start_time)
    return sol 

def generate_relu_dict2D(N1,N2):
    
    theta = np.linspace(0, 2*pi, N1, endpoint= False).reshape(N1,1)
    W1 = np.cos(theta)
    W2 = np.sin(theta)
    W = np.concatenate((W1,W2),1) # N1 x 2
    b = np.linspace(-1.42, 1.42, N2,endpoint=False).reshape(N2,1)
    
    index1 = np.arange(N1)
    index2 = np.arange(N2)
    ordered_pairs = np.array(np.meshgrid(index1,index2,indexing='ij'))

    ordered_pairs = ordered_pairs.reshape(2,-1).T
    W = W[ordered_pairs[:,0],:]
    b = b[ordered_pairs[:,1],:]
    Wb = np.concatenate((W,b),1) # N1 x 3 
    Wb_tensor = torch.from_numpy(Wb) 
    return Wb_tensor

# Wb = generate_relu_dict2D(10,20).to(device)
# print(Wb.shape)

Sob = torch.quasirandom.SobolEngine(dimension =2, scramble= True, seed=None) 
def generate_relu_dict2D_QMC(s,N0):
    # add this method to your notes... otherwise you will forget it 
    # Generate randomized Sobol sequence 
    sample_list = [Sob.draw(N0).double() for _ in range(s)]
    samples = torch.cat(sample_list, dim=0)

    T =torch.tensor([[2*pi,0],[0,2.84]])

    shift = torch.tensor([0,-1.42]) 

    samples = samples@T + shift 

    theta = samples[:,0].reshape(s*N0,1)
    W1 = torch.cos(theta)
    W2 = torch.sin(theta)
    W = torch.cat((W1,W2),1) # N1 x 2
    # b = np.linspace(-1.42, 1.42, N2,endpoint=False).reshape(N2,1) 
    b = samples[:,1].reshape(s*N0,1)
    Wb = torch.cat((W,b),1) # N1 x 3 
    return Wb 

def generate_relu_dict4plusD_sphere(dim, s,N0): # 
    samples = torch.randn(s*N0,dim +1) 
    samples = samples/samples.norm(dim=1,keepdim=True)  
    Wb = samples 
    return Wb 

def OGAL2FittingReLU2D_QMC(my_model,target,s,N0,num_epochs,plot_freq, Nx, order, k =1, solver = "direct",plot = False): 
    """ Orthogonal greedy algorithm using 1D ReLU dictionary over [-pi,pi]
    Parameters
    ----------
    my_model: 
        nn model 
    target: 
        target function
    num_epochs: int 
        number of training epochs 
    integration_intervals: int 
        number of subintervals for piecewise numerical quadrature 

    Returns
    -------
    err: tensor 
        rank 1 torch tensor to record the L2 error history  
    model: 
        trained nn model 
    """
    #Todo Done
    integration_weights, integration_points = PiecewiseGQ2D_weights_points(Nx, order)
    integration_weights = integration_weights.to(device)
    integration_points = integration_points.to(device)

    err = torch.zeros(num_epochs+1)
    if my_model == None: 
        func_values = target(integration_points)
        num_neuron = 0

        list_b = []
        list_w = []
    else: 
        func_values = target(integration_points) - my_model(integration_points).detach()
        bias = my_model.fc1.bias.detach().data
        weights = my_model.fc1.weight.detach().data
        num_neuron = int(bias.size(0))

        list_b = list(bias)
        list_w = list(weights)
    
    # initial error Todo Done
    func_values_sqrd = func_values*func_values
    err[0]= torch.sum(func_values_sqrd*integration_weights)**0.5
    start_time = time.time()
    
    # print("using linear solver: ",solver)
    for i in range(num_epochs): 
#         relu_dict_parameters = generate_relu_dict2D_QMC(s,N0).to(device) 
        relu_dict_parameters = generate_relu_dict4plusD_sphere(dim=2,s=1,N0=N0).to(device) 
        # print("epoch: ",i+1, end = '\t')
        if num_neuron == 0: 
            func_values = target(integration_points)
        else: 
            func_values = target(integration_points) - my_model(integration_points).detach()

        # Argmax subproblem 
        weight_func_values = func_values*integration_weights 
        basis_values = (F.relu( torch.matmul(integration_points,relu_dict_parameters[:,0:2].T ) - relu_dict_parameters[:,2])**k).T # uses broadcasting
        output = torch.abs(torch.matmul(basis_values,weight_func_values)) # 
        neuron_index = torch.argmax(output.flatten())
        list_w.append(relu_dict_parameters[neuron_index,0:2]) # 
        list_b.append(-relu_dict_parameters[neuron_index,2])

        num_neuron += 1
        my_model = model(2,num_neuron,1,k).to(device)
        w_tensor = torch.stack(list_w, 0 ) 
        b_tensor = torch.tensor(list_b)
        my_model.fc1.weight.data[:,:] = w_tensor[:,:]
        my_model.fc1.bias.data[:] = b_tensor[:]

        sol = minimize_linear_layer_explicit_assemble(my_model,target,integration_weights,integration_points,solver="ls")
        
        my_model.fc2.weight.data[0,:] = sol[:]
        if (i+1)%plot_freq == 0 and plot: 
            plot_2D(my_model.cpu())
            my_model = my_model.to(device)

        func_values = target(integration_points) - my_model(integration_points).detach()
        func_values_sqrd = func_values*func_values

        #Todo Done 
        err[i+1]= torch.sum(func_values_sqrd*integration_weights)**0.5

    return err, my_model

#compute max and inf for wx+b for each neuron of my_model 
def adjust_neuron_position(my_model):
    counter = 0 
    positions = torch.tensor([[0.,0.],[0.,1.],[1.,1.],[1.,0.]])
    neuron_num = my_model.fc1.bias.size(0)
    for i in range(neuron_num): 
        w = my_model.fc1.weight.data[i:i+1,:]
        b = my_model.fc1.bias.data[i]
    #     print(w,b)
        values = torch.matmul(positions,w.T) # + b
        left_end = - torch.max(values)
        right_end = - torch.min(values)
        offset = (right_end - left_end)/50
        if b <= left_end + offset/2 : 
            b = torch.rand(1)*(right_end - left_end - offset) + left_end + offset/2 
            my_model.fc1.bias.data[i] = b 
        if b >= right_end - offset/2 :
            if counter < 3:
#                 print("here")
                counter += 1
            else: # 3 or more 
                b = torch.rand(1)*(right_end - left_end - offset) + left_end + offset/2 
                my_model.fc1.bias.data[i] = b 
    return my_model

def Full_Random_DNSSC2D_QMCOGA(my_model,target,s,N0,nn_size, num_epochs,plot_freq = 10, Nx = 100, order =3, k = 1, plot = False):
    """
    Use OGA with a ReLU dictionary to adjust a random neuron to fit the target function better. 
    Parameters
    ----------
    my_model: 
        nn model
    target: 
        target function
    relu_dict_parameters:
        relu dictionary used for 1D ReLU-OGA
    num_epochs: int
        number of times for correcting neurons
    integration_intervals: int  
        number of subintervals for piecewise numerical quadrature
    k: int
        power of ReLU function
    Returns
    -------
    err: tensor
        rank 1 torch tensor to record the L2 error history
    nodes_per_epoch: tensor
        rank 2 torch tensor to record the grid distribution history 
    my_model:
        trained nn model
    """
    # 0. Weights and points for piecewise numerical quadrature
    integration_weights, integration_points = PiecewiseGQ2D_weights_points(Nx, order) 
    integration_weights = integration_weights.to(device)
    integration_points = integration_points.to(device)
    # 1. Constructive stage 
    err_list = []  
    if my_model == None:
        # use OGA to construct the nn 
        print("using OGA")
        err_OGA, my_model = OGAL2FittingReLU2D_QMC(my_model,target,s,N0,nn_size,plot_freq = nn_size, Nx = Nx, order = order, k = k, solver = 'ls',plot = plot)
        for i in range(len(err_OGA[:-1])): 
            err_list.append(err_OGA[i])
    else: 
#         sol = minimize_linear_layer(my_model,target,solver = 'direct', Nx = Nx, order = order)
        sol = minimize_linear_layer_explicit_assemble(my_model,target,integration_weights,integration_points,solver="ls")
        my_model.fc2.weight.data[0,:] = sol[:]

    num_neurons = my_model.fc1.bias.size(0)


    func_values = ( my_model(integration_points) - target(integration_points) )**2 
    err_init = torch.sum(integration_weights * func_values)**0.5 
    err_list.append(err_init)

    # 2. Iterative stage 
    flag = torch.zeros(num_neurons)
    for epoch in range(num_epochs): 
        if (epoch+1)%10 == 0:
            print("num_epochs: ",epoch+1, end = '\t', flush=True)

        are_all_ones = torch.all(torch.eq(flag, 1))
        if are_all_ones:
            print("Program terminated. Algorithm optimum reached.")
            break
        neuron_pos = torch.randint(num_neurons,(1,))
        while flag[neuron_pos] == 1:
            neuron_pos = torch.randint(num_neurons,(1,))
        
        my_model_weight = my_model.fc1.weight.data[:,:]
        my_model_bias = my_model.fc1.bias.data[:] 

        indices= torch.arange(my_model_bias.size(0)) 
        model_candidate = model(2,num_neurons - 1,1).to(device) # dimension 
        model_candidate.fc1.weight.data[:,:] = my_model_weight[indices != neuron_pos]
        model_candidate.fc1.bias.data[:] = my_model_bias[indices != neuron_pos]
#         sol = minimize_linear_layer(model_candidate,target,solver = 'ls', Nx = Nx, order = order) # project to correct
        sol = minimize_linear_layer_explicit_assemble(model_candidate,target,integration_weights,integration_points,solver="ls")
#         my_model.fc2.weight.data[0,:] = sol[:]
        model_candidate.fc2.weight.data[0,:] = sol[:] 
        err_OGA, model_candidate = OGAL2FittingReLU2D_QMC(model_candidate,target,s,N0,1,plot_freq = 3, Nx = Nx, order = order, k = k, solver = 'ls')

        # determine if the candidate is good by computing the error  
        diff1_sqrd = (target(integration_points) - my_model(integration_points).detach())**2
        diff2_sqrd = (target(integration_points) - model_candidate(integration_points).detach())**2  
        E1 = torch.sum(diff1_sqrd*integration_weights)**0.5   # error for my_model 
        E2 = torch.sum(diff2_sqrd*integration_weights)**0.5  # error for model_candidate
        if E2 < E1 - 1e-15: #good 
            my_model.fc1.weight.data[:,:] = model_candidate.fc1.weight.data[:,:]
            my_model.fc1.bias.data[:] = model_candidate.fc1.bias.data[:]
            my_model.fc2.weight.data[0,:] = model_candidate.fc2.weight.data[0,:]
            err_list.append(E2)
            flag[:] = 0 
            flag[neuron_pos] = 1  
        else: # bad
            flag[neuron_pos] = 1
            err_list.append(E1) 
            if (epoch+1)%plot_freq == 0 and plot: 
                print("plot something")
            continue
        
        if (epoch+1)%plot_freq == 0 and plot: 
            print("plot something")
    err_list = torch.tensor(err_list)
    print() 
    return err_list, my_model 


In [ ]:

if __name__ == "__main__": 
    # def target(x):
    #     return 10*(torch.sin(x) + torch.sin(3*x)) + 10*( \
    #             torch.sin(4*x) + torch.sin(9*x) + torch.sin(13*x)- torch.sin(x) - torch.sin(3*x) \
    #             )* torch.heaviside(x,torch.tensor([0.0]))

    def target(x):
        z = torch.cos(4 * pi *x[:,0:1]) * torch.cos(2 * pi *x[:,1:2])
        return z 
    function_name = 'cos4pix1cos2pix2'
    load_oga = False 
    load_init = False 
    model_none = False 
    plot = False 
    save_data = False 
    relu_k = 1 

    start_time = time.time() 
    exponent = 9 
    neuron_num_list = [2**ii for ii in range(2,exponent + 1)]
    num_trials = 10  
    err_trials = torch.zeros(len(neuron_num_list),num_trials)
    for i, num_neurons in enumerate(neuron_num_list):
        for trial in range(num_trials):
            num_epochs = num_neurons * 2  ###  
            print("num neurons: ",num_neurons) 
            for N1 in [2**7]: 
                s = 2**2
                N = s * N1 
                print( "N: ", N) 
                nn_size = num_neurons    
                plot = False 
                plot_freq = num_epochs 
                Nx = 100 
                order = 3 

                my_model = model(2,num_neurons,1,k=relu_k).to(device)
                folder_name = 'data/'
                if load_oga: 
                    my_model.load_state_dict(torch.load('data-oga/model_OGAReLU_quadratic_N_1024_epochs_{}.pt'.format(num_neurons))) 
                elif load_init: 
                    filename = folder_name +'model_init1_neuron_{}.pt'.format(num_neurons)
                    my_model.load_state_dict(torch.load(filename))
                elif model_none:
                    my_model = None 
                else: 
                    # initialize with the RFM 
                    integration_weights, integration_points = PiecewiseGQ2D_weights_points(100, 3)  
    #                 my_model = adjust_neuron_position(my_model.cpu()).to(device)
                    sol = minimize_linear_layer_explicit_assemble(my_model,target,integration_weights,integration_points,solver="ls") 
                    my_model.fc2.weight.data[0,:] = sol[:]
    #                 a = minimize_linear_layer(my_model,target)
    #                 my_model.fc2.weight.data[0,:] = a[:] 
                err_list, my_model  = Full_Random_DNSSC2D_QMCOGA(my_model,target,s,N1,nn_size, num_epochs,plot_freq,Nx = Nx, order = order, k = relu_k, plot=plot)
                err_trials[i,trial] = err_list[-1]
                if save_data: 
                    folder_name = 'data/' 
                    filename = folder_name + 'err_{}_N_{}_neuron_{}_epochs_{}_randomized.pt'.format(function_name,s*N, num_neurons,num_epochs)
                    torch.save(err_list, filename)
                    filename = folder_name +'model_{}_N_{}_neuron_{}_epochs_{}_randomized.pt'.format(function_name,s*N, num_neurons,num_epochs)
                    torch.save(my_model.state_dict(), filename)

                # Plot 2. Grid evolution 
                if plot: 
                    plot_2D(my_model.cpu()) 

        print("time taken: ",time.time() - start_time) 

num neurons:  4
N:  512
assembling the matrix time taken:  0.0003578662872314453
solving Ax = b time taken:  0.0008149147033691406
assembling the matrix time taken:  0.0002772808074951172
solving Ax = b time taken:  0.0008332729339599609
assembling the matrix time taken:  0.00021147727966308594
solving Ax = b time taken:  0.0008313655853271484
assembling the matrix time taken:  0.00020360946655273438
solving Ax = b time taken:  0.0008759498596191406
assembling the matrix time taken:  0.00020766258239746094
solving Ax = b time taken:  0.0008466243743896484
assembling the matrix time taken:  0.00020170211791992188
solving Ax = b time taken:  0.0008733272552490234
assembling the matrix time taken:  0.00019669532775878906
solving Ax = b time taken:  0.0008618831634521484
assembling the matrix time taken:  0.00020241737365722656
solving Ax = b time taken:  0.0008776187896728516
assembling the matrix time taken:  0.0001957416534423828
solving Ax = b time taken:  0.0008671283721923828
assembl

assembling the matrix time taken:  0.00020265579223632812
solving Ax = b time taken:  0.0006563663482666016
assembling the matrix time taken:  0.0001964569091796875
solving Ax = b time taken:  0.0006685256958007812
assembling the matrix time taken:  0.00021076202392578125
solving Ax = b time taken:  0.0006933212280273438
assembling the matrix time taken:  0.0001952648162841797
solving Ax = b time taken:  0.0006721019744873047
assembling the matrix time taken:  0.00020170211791992188
solving Ax = b time taken:  0.0006821155548095703
Program terminated. Algorithm optimum reached.

num neurons:  4
N:  512
assembling the matrix time taken:  0.00023365020751953125
solving Ax = b time taken:  0.0006458759307861328
assembling the matrix time taken:  0.00023221969604492188
solving Ax = b time taken:  0.0006325244903564453
assembling the matrix time taken:  0.00022149085998535156
solving Ax = b time taken:  0.0006268024444580078
assembling the matrix time taken:  0.00020265579223632812
solving 

assembling the matrix time taken:  0.00023698806762695312
solving Ax = b time taken:  0.0007467269897460938
assembling the matrix time taken:  0.00023746490478515625
solving Ax = b time taken:  0.0007259845733642578
assembling the matrix time taken:  0.00023293495178222656
solving Ax = b time taken:  0.0007071495056152344
assembling the matrix time taken:  0.0002105236053466797
solving Ax = b time taken:  0.0007534027099609375
assembling the matrix time taken:  0.00019598007202148438
solving Ax = b time taken:  0.0007417201995849609
assembling the matrix time taken:  0.00020003318786621094
solving Ax = b time taken:  0.0007655620574951172
assembling the matrix time taken:  0.0001957416534423828
solving Ax = b time taken:  0.00075531005859375
assembling the matrix time taken:  0.0002009868621826172
solving Ax = b time taken:  0.000762939453125
assembling the matrix time taken:  0.0002110004425048828
solving Ax = b time taken:  0.000728607177734375
assembling the matrix time taken:  0.00

solving Ax = b time taken:  0.0007288455963134766
assembling the matrix time taken:  0.00021219253540039062
solving Ax = b time taken:  0.0007460117340087891
assembling the matrix time taken:  0.0001964569091796875
solving Ax = b time taken:  0.0007355213165283203
assembling the matrix time taken:  0.0002002716064453125
solving Ax = b time taken:  0.0007500648498535156
assembling the matrix time taken:  0.00019598007202148438
solving Ax = b time taken:  0.0007486343383789062
assembling the matrix time taken:  0.00020122528076171875
solving Ax = b time taken:  0.0007493495941162109
assembling the matrix time taken:  0.0002079010009765625
solving Ax = b time taken:  0.0007305145263671875
assembling the matrix time taken:  0.0002105236053466797
solving Ax = b time taken:  0.0007596015930175781
assembling the matrix time taken:  0.00019502639770507812
solving Ax = b time taken:  0.0007581710815429688
assembling the matrix time taken:  0.00020003318786621094
solving Ax = b time taken:  0.00

assembling the matrix time taken:  0.00021076202392578125
solving Ax = b time taken:  0.0007512569427490234
num_epochs:  10	assembling the matrix time taken:  0.00021219253540039062
solving Ax = b time taken:  0.0007195472717285156
assembling the matrix time taken:  0.0002155303955078125
solving Ax = b time taken:  0.0007479190826416016
assembling the matrix time taken:  0.00020432472229003906
solving Ax = b time taken:  0.0007658004760742188
assembling the matrix time taken:  0.0002205371856689453
solving Ax = b time taken:  0.0007405281066894531
assembling the matrix time taken:  0.0002033710479736328
solving Ax = b time taken:  0.0007688999176025391
assembling the matrix time taken:  0.00021123886108398438
solving Ax = b time taken:  0.0007655620574951172
assembling the matrix time taken:  0.00019478797912597656
solving Ax = b time taken:  0.0007655620574951172
assembling the matrix time taken:  0.000202178955078125
solving Ax = b time taken:  0.0007724761962890625
assembling the ma

...

assembling the matrix time taken:  0.0002117156982421875
solving Ax = b time taken:  0.15449833869934082
assembling the matrix time taken:  0.00021696090698242188
solving Ax = b time taken:  0.15503382682800293
assembling the matrix time taken:  0.00020837783813476562
solving Ax = b time taken:  0.15488386154174805
assembling the matrix time taken:  0.00021028518676757812
solving Ax = b time taken:  0.15503883361816406
assembling the matrix time taken:  0.0002086162567138672
solving Ax = b time taken:  0.15467405319213867
assembling the matrix time taken:  0.00021457672119140625
solving Ax = b time taken:  0.15577387809753418
assembling the matrix time taken:  0.0002117156982421875
solving Ax = b time taken:  0.15463471412658691
assembling the matrix time taken:  0.00021338462829589844
solving Ax = b time taken:  0.15491008758544922
assembling the matrix time taken:  0.00021505355834960938
solving Ax = b time taken:  0.15442609786987305
assembling the matrix time taken:  0.000221014022

solving Ax = b time taken:  0.15503573417663574
num_epochs:  610	assembling the matrix time taken:  0.00021648406982421875
solving Ax = b time taken:  0.15533804893493652
assembling the matrix time taken:  0.00022220611572265625
solving Ax = b time taken:  0.1549086570739746
assembling the matrix time taken:  0.00020885467529296875
solving Ax = b time taken:  0.1551060676574707
assembling the matrix time taken:  0.0002186298370361328
solving Ax = b time taken:  0.15523743629455566
assembling the matrix time taken:  0.00021266937255859375
solving Ax = b time taken:  0.15474462509155273
assembling the matrix time taken:  0.00021266937255859375
solving Ax = b time taken:  0.15575170516967773
assembling the matrix time taken:  0.00023365020751953125
solving Ax = b time taken:  0.15521931648254395
assembling the matrix time taken:  0.0002129077911376953
solving Ax = b time taken:  0.1804659366607666
assembling the matrix time taken:  0.00022721290588378906
solving Ax = b time taken:  0.1555

assembling the matrix time taken:  0.00021767616271972656
solving Ax = b time taken:  0.15621185302734375
assembling the matrix time taken:  0.0002186298370361328
solving Ax = b time taken:  0.15511178970336914
assembling the matrix time taken:  0.0002224445343017578
solving Ax = b time taken:  0.15476202964782715
num_epochs:  650	assembling the matrix time taken:  0.0002205371856689453
solving Ax = b time taken:  0.15565180778503418
assembling the matrix time taken:  0.0002117156982421875
solving Ax = b time taken:  0.15507078170776367
assembling the matrix time taken:  0.00020694732666015625
solving Ax = b time taken:  0.15474700927734375
assembling the matrix time taken:  0.0002124309539794922
solving Ax = b time taken:  0.15648746490478516
assembling the matrix time taken:  0.00021648406982421875
solving Ax = b time taken:  0.1552901268005371
assembling the matrix time taken:  0.00021576881408691406
solving Ax = b time taken:  0.15571188926696777
assembling the matrix time taken:  

solving Ax = b time taken:  0.15450811386108398
assembling the matrix time taken:  0.00021314620971679688
solving Ax = b time taken:  0.15600061416625977
assembling the matrix time taken:  0.00022125244140625
solving Ax = b time taken:  0.15481948852539062
assembling the matrix time taken:  0.00021266937255859375
solving Ax = b time taken:  0.15520739555358887
assembling the matrix time taken:  0.00021123886108398438
solving Ax = b time taken:  0.15487384796142578
assembling the matrix time taken:  0.00021004676818847656
solving Ax = b time taken:  0.1558220386505127
num_epochs:  690	assembling the matrix time taken:  0.000213623046875
solving Ax = b time taken:  0.15473175048828125
assembling the matrix time taken:  0.0002162456512451172
solving Ax = b time taken:  0.1550004482269287
assembling the matrix time taken:  0.0002105236053466797
solving Ax = b time taken:  0.1544349193572998
assembling the matrix time taken:  0.00021886825561523438
solving Ax = b time taken:  0.154974460601

assembling the matrix time taken:  0.00020933151245117188
solving Ax = b time taken:  0.155747652053833
assembling the matrix time taken:  0.0002148151397705078
solving Ax = b time taken:  0.15622878074645996


In [ ]:
print(err_trials.mean(dim = 1))
filename = "iterative_OGA_error_trials.pt"
errrrr = torch.load(filename)
# torch.save(err_trials,filename)

In [44]:
errrrr = torch.load(filename)
print(errrrr)

tensor([[0.48118964, 0.49739999],
        [0.41007423, 0.42517062],
        [0.12750310, 0.15719827],
        [0.06611073, 0.06448710]])


In [9]:
def show_convergence_order_latex(err_l2,exponent,k=1,d=1): 
    neuron_nums = [2**j for j in range(2,exponent+1)]
    err_list = [err_l2[i] for i in neuron_nums ]
    l2_order = -1/2-(2*k + 1)/(2*d)
    print("neuron num  & \t $\\|u-u_n \\|_{{L^2}}$ & \t order $O(n^{{{:.2f}}})$  \\\\ \\hline \\hline ".format(l2_order))
    for i, item in enumerate(err_list):
        if i == 0: 
            print("{} \t\t & {:.6f} &\t\t *  \\\ \hline  \n".format(neuron_nums[i],item) )   
        else: 
            print("{} \t\t &  {:.3e} &  \t\t {:.2f} \\\ \hline  \n".format(neuron_nums[i],item,np.log(err_list[i-1]/err_list[i])/np.log(2) ) )

def show_convergence_order_latex_mod(err_list,exponent,k=1,d=1): 
    neuron_nums = [2**j for j in range(2,exponent+1)]
#     err_list = [err_l2[i] for i in neuron_nums ]
    l2_order = -1/2-(2*k + 1)/(2*d)
    print("neuron num  & \t $\\|u-u_n \\|_{{L^2}}$ & \t order $O(n^{{{:.2f}}})$  \\\\ \\hline \\hline ".format(l2_order))
    for i, item in enumerate(err_list):
        if i == 0: 
            print("{} \t\t & {:.6f} &\t\t *  \\\ \hline  \n".format(neuron_nums[i],item) )   
        else: 
            print("{} \t\t &  {:.3e} &  \t\t {:.2f} \\\ \hline  \n".format(neuron_nums[i],item,np.log(err_list[i-1]/err_list[i])/np.log(2) ) )


In [11]:



if __name__ == "__main__": 
    # def target(x):
    #     return 10*(torch.sin(x) + torch.sin(3*x)) + 10*( \
    #             torch.sin(4*x) + torch.sin(9*x) + torch.sin(13*x)- torch.sin(x) - torch.sin(3*x) \
    #             )* torch.heaviside(x,torch.tensor([0.0]))

    def target(x):
        z = torch.cos(4 * pi *x[:,0:1]) * torch.cos(2 * pi *x[:,1:2])
        return z 
    

    Nx = 100 
    order = 3 
    num_trials = 10  
    exponent = 9
    neuron_num_list = [2**ii for ii in range(2,exponent + 1)]
    err_trials = torch.zeros(len(neuron_num_list),num_trials) 
    N0 = 2**8 
    num_epochs = 2**exponent
    plot_freq = num_epochs + 1
    
    for trial in range(num_trials): 
        s = 1 
        N = s*N0
        relu_k = 1
        my_model = None 
        err, my_model = OGAL2FittingReLU2D_QMC(my_model,target,s,N0,num_epochs,plot_freq, Nx, order, k =relu_k, solver = "direct",plot = False)
        for ii, index, in enumerate(neuron_num_list): 
            err_trials[ii,trial] = err[index]

assembling the matrix time taken:  0.0003871917724609375
solving Ax = b time taken:  0.00033664703369140625
assembling the matrix time taken:  0.00043845176696777344
solving Ax = b time taken:  0.00039768218994140625
assembling the matrix time taken:  0.00035858154296875
solving Ax = b time taken:  0.0007517337799072266
assembling the matrix time taken:  0.00034308433532714844
solving Ax = b time taken:  0.0008234977722167969
assembling the matrix time taken:  0.00032138824462890625
solving Ax = b time taken:  0.0008296966552734375
assembling the matrix time taken:  0.0003647804260253906
solving Ax = b time taken:  0.0008096694946289062
assembling the matrix time taken:  0.00032591819763183594
solving Ax = b time taken:  0.0008969306945800781
assembling the matrix time taken:  0.0003190040588378906
solving Ax = b time taken:  0.0008742809295654297
assembling the matrix time taken:  0.00041103363037109375
solving Ax = b time taken:  0.0008716583251953125
assembling the matrix time taken

assembling the matrix time taken:  0.00034117698669433594
solving Ax = b time taken:  0.011516571044921875
assembling the matrix time taken:  0.00033926963806152344
solving Ax = b time taken:  0.011182308197021484
assembling the matrix time taken:  0.00031113624572753906
solving Ax = b time taken:  0.01162409782409668
assembling the matrix time taken:  0.00033402442932128906
solving Ax = b time taken:  0.011682987213134766
assembling the matrix time taken:  0.0003209114074707031
solving Ax = b time taken:  0.011371612548828125
assembling the matrix time taken:  0.0003380775451660156
solving Ax = b time taken:  0.011703729629516602
assembling the matrix time taken:  0.0003247261047363281
solving Ax = b time taken:  0.0119476318359375
assembling the matrix time taken:  0.0003566741943359375
solving Ax = b time taken:  0.011456489562988281
assembling the matrix time taken:  0.00031375885009765625
solving Ax = b time taken:  0.011695384979248047
assembling the matrix time taken:  0.0003654

assembling the matrix time taken:  0.00033974647521972656
solving Ax = b time taken:  0.025321245193481445
assembling the matrix time taken:  0.0003917217254638672
solving Ax = b time taken:  0.025271892547607422
assembling the matrix time taken:  0.00032329559326171875
solving Ax = b time taken:  0.025583744049072266
assembling the matrix time taken:  0.00033211708068847656
solving Ax = b time taken:  0.025470972061157227
assembling the matrix time taken:  0.00032591819763183594
solving Ax = b time taken:  0.025717973709106445
assembling the matrix time taken:  0.0003604888916015625
solving Ax = b time taken:  0.02567744255065918
assembling the matrix time taken:  0.0003216266632080078
solving Ax = b time taken:  0.02583932876586914
assembling the matrix time taken:  0.0003230571746826172
solving Ax = b time taken:  0.025714874267578125
assembling the matrix time taken:  0.00033855438232421875
solving Ax = b time taken:  0.02586841583251953
assembling the matrix time taken:  0.0003368

assembling the matrix time taken:  0.0006754398345947266
solving Ax = b time taken:  0.045087575912475586
assembling the matrix time taken:  0.0003485679626464844
solving Ax = b time taken:  0.04529452323913574
assembling the matrix time taken:  0.00032591819763183594
solving Ax = b time taken:  0.045900583267211914
assembling the matrix time taken:  0.00031280517578125
solving Ax = b time taken:  0.04584360122680664
assembling the matrix time taken:  0.0003151893615722656
solving Ax = b time taken:  0.0459599494934082
assembling the matrix time taken:  0.0003352165222167969
solving Ax = b time taken:  0.04580116271972656
assembling the matrix time taken:  0.00034618377685546875
solving Ax = b time taken:  0.04597926139831543
assembling the matrix time taken:  0.00032448768615722656
solving Ax = b time taken:  0.046005964279174805
assembling the matrix time taken:  0.0003216266632080078
solving Ax = b time taken:  0.04596757888793945
assembling the matrix time taken:  0.000340223312377

assembling the matrix time taken:  0.00032973289489746094
solving Ax = b time taken:  0.08999252319335938
assembling the matrix time taken:  0.0003292560577392578
solving Ax = b time taken:  0.09015488624572754
assembling the matrix time taken:  0.00035572052001953125
solving Ax = b time taken:  0.09069442749023438
assembling the matrix time taken:  0.0003390312194824219
solving Ax = b time taken:  0.09082579612731934
assembling the matrix time taken:  0.0003285408020019531
solving Ax = b time taken:  0.09037399291992188
assembling the matrix time taken:  0.0003123283386230469
solving Ax = b time taken:  0.09062981605529785
assembling the matrix time taken:  0.0003352165222167969
solving Ax = b time taken:  0.09043002128601074
assembling the matrix time taken:  0.0003376007080078125
solving Ax = b time taken:  0.09096431732177734
assembling the matrix time taken:  0.0003261566162109375
solving Ax = b time taken:  0.09075760841369629
assembling the matrix time taken:  0.0003228187561035

...

solving Ax = b time taken:  0.02483391761779785
assembling the matrix time taken:  0.00034689903259277344
solving Ax = b time taken:  0.02489328384399414
assembling the matrix time taken:  0.000293731689453125
solving Ax = b time taken:  0.024797916412353516
assembling the matrix time taken:  0.0002944469451904297
solving Ax = b time taken:  0.02495741844177246
assembling the matrix time taken:  0.0003407001495361328
solving Ax = b time taken:  0.024921417236328125
assembling the matrix time taken:  0.000335693359375
solving Ax = b time taken:  0.02504897117614746
assembling the matrix time taken:  0.0003230571746826172
solving Ax = b time taken:  0.025061845779418945
assembling the matrix time taken:  0.0003142356872558594
solving Ax = b time taken:  0.0253145694732666
assembling the matrix time taken:  0.00032591819763183594
solving Ax = b time taken:  0.025114059448242188
assembling the matrix time taken:  0.000347137451171875
solving Ax = b time taken:  0.025359392166137695
assembl

solving Ax = b time taken:  0.04491925239562988
assembling the matrix time taken:  0.0003333091735839844
solving Ax = b time taken:  0.04498171806335449
assembling the matrix time taken:  0.0003228187561035156
solving Ax = b time taken:  0.04503965377807617
assembling the matrix time taken:  0.00032258033752441406
solving Ax = b time taken:  0.04490780830383301
assembling the matrix time taken:  0.0003275871276855469
solving Ax = b time taken:  0.04532170295715332
assembling the matrix time taken:  0.00032401084899902344
solving Ax = b time taken:  0.045189619064331055
assembling the matrix time taken:  0.000331878662109375
solving Ax = b time taken:  0.04551863670349121
assembling the matrix time taken:  0.0003116130828857422
solving Ax = b time taken:  0.0451204776763916
assembling the matrix time taken:  0.0003523826599121094
solving Ax = b time taken:  0.04549860954284668
assembling the matrix time taken:  0.0003650188446044922
solving Ax = b time taken:  0.04551053047180176
assemb

solving Ax = b time taken:  0.06987452507019043
assembling the matrix time taken:  0.00034618377685546875
solving Ax = b time taken:  0.06973052024841309
assembling the matrix time taken:  0.00033402442932128906
solving Ax = b time taken:  0.07012820243835449
assembling the matrix time taken:  0.0003223419189453125
solving Ax = b time taken:  0.06978344917297363
assembling the matrix time taken:  0.0003120899200439453
solving Ax = b time taken:  0.07044720649719238
assembling the matrix time taken:  0.00032138824462890625
solving Ax = b time taken:  0.07043719291687012
assembling the matrix time taken:  0.0003364086151123047
solving Ax = b time taken:  0.07066559791564941
assembling the matrix time taken:  0.0003237724304199219
solving Ax = b time taken:  0.07024121284484863
assembling the matrix time taken:  0.00034999847412109375
solving Ax = b time taken:  0.07056498527526855
assembling the matrix time taken:  0.0003333091735839844
solving Ax = b time taken:  0.07040929794311523
ass

solving Ax = b time taken:  0.10003018379211426
assembling the matrix time taken:  0.0003123283386230469
solving Ax = b time taken:  0.12470293045043945
assembling the matrix time taken:  0.00033402442932128906
solving Ax = b time taken:  0.12508177757263184
assembling the matrix time taken:  0.0003352165222167969
solving Ax = b time taken:  0.1252744197845459
assembling the matrix time taken:  0.00033593177795410156
solving Ax = b time taken:  0.1263294219970703
assembling the matrix time taken:  0.0003254413604736328
solving Ax = b time taken:  0.1253042221069336
assembling the matrix time taken:  0.000324249267578125
solving Ax = b time taken:  0.12540817260742188
assembling the matrix time taken:  0.00032520294189453125
solving Ax = b time taken:  0.12543821334838867
assembling the matrix time taken:  0.0003249645233154297
solving Ax = b time taken:  0.1255204677581787
assembling the matrix time taken:  0.00030922889709472656
solving Ax = b time taken:  0.12569761276245117
assembli

solving Ax = b time taken:  0.16396164894104004
assembling the matrix time taken:  0.0003635883331298828
solving Ax = b time taken:  0.1640486717224121
assembling the matrix time taken:  0.0003147125244140625
solving Ax = b time taken:  0.16420674324035645
assembling the matrix time taken:  0.00030350685119628906
solving Ax = b time taken:  0.164750337600708
assembling the matrix time taken:  0.00034046173095703125
solving Ax = b time taken:  0.1647486686706543
assembling the matrix time taken:  0.00032210350036621094
solving Ax = b time taken:  0.16472935676574707
assembling the matrix time taken:  0.0003387928009033203
solving Ax = b time taken:  0.16507935523986816
assembling the matrix time taken:  0.0003020763397216797
solving Ax = b time taken:  0.16539478302001953
assembling the matrix time taken:  0.00033736228942871094
solving Ax = b time taken:  0.1653754711151123
assembling the matrix time taken:  0.00035643577575683594
solving Ax = b time taken:  0.16528010368347168
assembl

In [12]:
filename = "OGA_error_trials.pt"
torch.save(err_trials,filename)
err_mean_OGA = err_trials.mean(dim = 1)
show_convergence_order_latex_mod(err_mean_OGA,exponent,k=relu_k,d=2)

neuron num  & 	 $\|u-u_n \|_{L^2}$ & 	 order $O(n^{-1.25})$  \\ \hline \hline 
4 		 & 0.489109 &		 *  \\ \hline  

8 		 &  4.138e-01 &  		 0.24 \\ \hline  

16 		 &  2.043e-01 &  		 1.02 \\ \hline  

32 		 &  8.694e-02 &  		 1.23 \\ \hline  

64 		 &  3.435e-02 &  		 1.34 \\ \hline  

128 		 &  1.428e-02 &  		 1.27 \\ \hline  

256 		 &  5.614e-03 &  		 1.35 \\ \hline  

512 		 &  2.150e-03 &  		 1.38 \\ \hline  



In [54]:
filename = "iterative_OGA_error_trials.pt"
errrrr = torch.load(filename)
err_mean = errrrr.mean(dim = 1)
print(err_mean)
exponent = 9 
show_convergence_order_latex_mod(err_mean,exponent,k=relu_k,d=2)

tensor([0.49098274, 0.39337682, 0.18550223, 0.07641473, 0.02972842, 0.01247044,
        0.00491376, 0.00192424])
neuron num  & 	 $\|u-u_n \|_{L^2}$ & 	 order $O(n^{-1.25})$  \\ \hline \hline 
4 		 & 0.490983 &		 *  \\ \hline  

8 		 &  3.934e-01 &  		 0.32 \\ \hline  

16 		 &  1.855e-01 &  		 1.08 \\ \hline  

32 		 &  7.641e-02 &  		 1.28 \\ \hline  

64 		 &  2.973e-02 &  		 1.36 \\ \hline  

128 		 &  1.247e-02 &  		 1.25 \\ \hline  

256 		 &  4.914e-03 &  		 1.34 \\ \hline  

512 		 &  1.924e-03 &  		 1.35 \\ \hline  

